In [18]:
import pandas as pd
import geopandas as gpd
import os
import matplotlib.pyplot as plt
import elevation
import rasterio
from rasterio.plot import show
from rasterstats import zonal_stats

##### Set the path:

In [19]:
folder = os.path.abspath(r'C:\Users\phwh9568\Zips')

#### Import US zip code tabulation areas shapefile into a geodataframe

In [2]:
zips = gpd.read_file('zip_codes/tl_2018_us_zcta510.shp')

#### Import zip codes from study into a dataframe    
Also renaming the column to be consistent w/ shapefile's naming convention

In [5]:
med_zips = pd.read_csv('med_zips.csv' , dtype={'Zip':str})
med_zips.rename(columns={'Zip': 'ZCTA5CE10'}, inplace=True)

#### Check out zip codes from input list that are not present in the ZCTA shapefile:
This probably means these are PO Boxes and not tabulate-able areas

In [11]:
full_zip_list = zips['ZCTA5CE10'].to_list()
med_zip_list = med_zips['ZCTA5CE10'].to_list()
no_zip_list = []
for med_zip in med_zip_list:
    if med_zip in full_zip_list:
        pass
    else:
        no_zip_list.append(med_zip)
print(no_zip_list)

['89504', '88031', '87547', '87502', '87184', '87174', '82605', '82345', '82003', '81848', '81502', '80937', '80934', '80933', '80932', '80931', '80901', '80614', '80539', '80502', '80306', '80217', '80155', '80047', '80044', '80041', '80035', '80034', '80006', '80001', '71228', '69363', '59107']


#### Merge the med_zip data to the zip geodataframe  
This gets rid of the zip codes not present in the study data

In [14]:
study_zips = zips.merge(med_zips, on='ZCTA5CE10')
print('Matched zips: ',len(study_zips))

Matched zips:  551


#### This function will be used later.
This function expands the around each zip code a smidge so imported data doesn't get cut off

In [15]:
def expander(bounds):
    bounds[0] = bounds[0] -.001
    bounds[1] = bounds[1] -.001
    bounds[2] = bounds[2] +.001
    bounds[3] = bounds[3] +.001
    bounds = tuple(i for i in bounds) 
    return bounds

#### Now we will iterate over each zip code and do the following:
1. Identify the zip code's bounding box
2. Expand the bounding box slightly
3. Download the elevation data for the area containing the zip code
4. Imports the new elevation data as 'dem' (dem=digital elevation model)
5. Calculates zonal statistics (the descriptive statistics for the portion of the dem that falls within the bounds of the zip code)
6. Writes the result to csv

In [36]:
def zonestats(index, row, zipbnds):
    global zs_dem
    bounds = zipbnds.iloc[index]
    bounds = [bounds[0], bounds[1], bounds[2], bounds[3]]
    bounds = expander(bounds)
    name = row['ZCTA5CE10']+'_DEM.tif'
    elevation.clip(bounds=bounds, output=os.path.join(folder, name))
    dem = rasterio.open(os.path.join(folder,name))
    array = dem.read(1)
    affine = dem.transform
    zs_dem = zonal_stats(row['geometry'], array, affine=affine, nodata=None, stats=['min', 'max', 'mean', 'median', 'majority'])
    return(zs_dem)

In [23]:
zip_bounds = study_zips.bounds

In [26]:
zip_bounds.iloc[0]

minx   -106.831631
miny     40.484827
maxx   -106.827086
maxy     40.488006
Name: 0, dtype: float64

In [37]:
for index, row in study_zips.iterrows():
    zonestats(index,row,zip_bounds)
    print(zs_dem)

[{'min': 2053.0, 'max': 2072.0, 'mean': 2059.112244897959, 'median': 2058.0, 'majority': 2056.0}]
[{'min': 2453.0, 'max': 3239.0, 'mean': 2735.9868308718246, 'median': 2712.0, 'majority': 3049.0}]
[{'min': 2356.0, 'max': 3944.0, 'mean': 2715.699565766806, 'median': 2625.0, 'majority': 2476.0}]
[{'min': 2541.0, 'max': 4070.0, 'mean': 3182.0597821586257, 'median': 3186.0, 'majority': 3145.0}]
[{'min': 2331.0, 'max': 3260.0, 'mean': 2649.061240621477, 'median': 2605.0, 'majority': 2538.0}]
[{'min': 1950.0, 'max': 3711.0, 'mean': 2530.3309400666044, 'median': 2449.0, 'majority': 2102.0}]
[{'min': 2060.0, 'max': 2061.0, 'mean': 2060.527777777778, 'median': 2061.0, 'majority': 2061.0}]
[{'min': 2300.0, 'max': 4137.0, 'mean': 2995.3657647694304, 'median': 2934.0, 'majority': 2424.0}]
[{'min': 1490.0, 'max': 1555.0, 'mean': 1519.4774454577969, 'median': 1518.0, 'majority': 1515.0}]
[{'min': 1518.0, 'max': 2154.0, 'mean': 1619.9537994102943, 'median': 1592.0, 'majority': 1546.0}]
[{'min': 1455.

KeyboardInterrupt: 

In [31]:
for index, row in study_zips.iterrows():
    b = zip_bounds.iloc[index]
    b = [b[0], b[1], b[2], b[3]]
    b = expander(b)
    print(row['geometry'])

POLYGON ((-106.831581 40.485741, -106.831432 40.485888, -106.831383 40.485938, -106.831343 40.485977, -106.831225 40.486093, -106.831186 40.486133, -106.831121 40.486196, -106.830928 40.486387, -106.830864 40.486451, -106.830851 40.486463, -106.830815 40.486498, -106.830803 40.486511, -106.830729 40.486596, -106.830512 40.486849, -106.830425 40.486933, -106.83032 40.487034, -106.830258 40.487095, -106.830118 40.487219, -106.829986 40.487316, -106.829921 40.487366, -106.829879 40.487414, -106.829809 40.487492, -106.829598 40.487727, -106.829529 40.487806, -106.829518 40.487817, -106.829488 40.487852, -106.829478 40.48786399999999, -106.829395 40.488006, -106.828049 40.48799899999999, -106.828041 40.487837, -106.828061 40.487666, -106.828067 40.487611, -106.828096 40.487358, -106.828128 40.487291, -106.828161 40.487244, -106.828216 40.4872, -106.828249 40.487182, -106.82835 40.487131, -106.828384 40.487114, -106.828471 40.487069, -106.828514 40.487048, -106.828708 40.486958, -106.828734 

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)




POLYGON ((-106.418779 35.825561, -106.418746 35.825595, -106.418519 35.825594, -106.417988 35.825494, -106.417952 35.825486, -106.417585 35.825404, -106.417418 35.825443, -106.417299 35.825507, -106.417269 35.825612, -106.417307 35.825733, -106.417453 35.825894, -106.417401 35.825937, -106.417318 35.826004, -106.417521 35.826223, -106.417595 35.826443, -106.417459 35.827076, -106.417479 35.827306, -106.417444 35.82741, -106.417388 35.82755, -106.417302 35.827731, -106.417283 35.82777, -106.413144 35.827776, -106.400596 35.827792, -106.400006 35.827793, -106.399627 35.827794, -106.399634 35.828233, -106.399542 35.82831, -106.399282 35.828538, -106.399256 35.828559, -106.399005 35.82871799999999, -106.398475 35.828939, -106.398174 35.829058, -106.397907 35.829118, -106.39751 35.829201, -106.397147 35.829315, -106.396861 35.82942, -106.396641 35.829496, -106.396517 35.829525, -106.396392 35.829527, -106.396271 35.829497, -106.396102 35.829424, -106.395667 35.8291, -106.395309 35.828824, 

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



POLYGON ((-107.476532 39.828267, -107.470729 39.828276, -107.466916 39.828282, -107.455365 39.828299, -107.45332 39.828302, -107.447518 39.828311, -107.445655 39.828319, -107.444368 39.82832399999999, -107.444051 39.828326, -107.443756 39.828327, -107.443461 39.828328, -107.434919 39.828363, -107.43177 39.828377, -107.431768 39.83024, -107.431766 39.832775, -107.431762 39.835832, -107.431761 39.837696, -107.431758 39.841087, -107.43175 39.851259, -107.431748 39.854651, -107.431701 39.860937, -107.431601 39.87498, -107.431608 39.879796, -107.431617 39.885873, -107.431619 39.886084, -107.431621 39.888328, -107.431628 39.89506799999999, -107.431632 39.896513, -107.431632 39.897315, -107.431633 39.898153, -107.431636 39.900666, -107.431638 39.901506, -107.431638 39.901733, -107.43164 39.902415, -107.431642 39.902644, -107.431649 39.907813, -107.431659 39.913768, -107.431659 39.913942, -107.431659 39.914116, -107.43166 39.914189, -107.43166 39.914359, -107.43166 39.91453, -107.431665 39.917

KeyboardInterrupt: 